In [1]:
import pandas as pd
import numpy as np

import re
import string

import nltk
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer

import gensim

In [2]:
#load dataset and preprocess
twt = pd.read_csv('train.csv')
twt = twt.set_index('id')

In [3]:
print(twt.info())
twt.loc[~twt['keyword'].isna()]

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7613 entries, 1 to 10873
Data columns (total 4 columns):
keyword     7552 non-null object
location    5080 non-null object
text        7613 non-null object
target      7613 non-null int64
dtypes: int64(1), object(3)
memory usage: 297.4+ KB
None


keyword                       location  \
id                                              
48      ablaze                     Birmingham   
49      ablaze  Est. September 2012 - Bristol   
50      ablaze                         AFRICA   
52      ablaze               Philadelphia, PA   
53      ablaze                     London, UK   
...        ...                            ...   
10830  wrecked                            NaN   
10831  wrecked              Vancouver, Canada   
10832  wrecked                        London    
10833  wrecked                        Lincoln   
10834  wrecked                            NaN   

                                                    text  target  
id                                                                
48     @bbcmtd Wholesale Markets ablaze http://t.co/l...       1  
49     We always try to bring the heavy. #metal #RT h...       0  
50     #AFRICANBAZE: Breaking news:Nigeria flag set a...       1  
52                    Crying out for more! Set me ablaze       0  
53     On plus side LOOK AT THE SKY LAST NIGHT IT WAS...       0  
...                                                  ...     ...  
10830   @jt_ruff23 @cameronhacker and I wrecked you both       0  
10831  Three days off from work and they've pretty mu...       0  
10832  #FX #forex #trading Cramer: Iger's 3 words tha...       0  
10833  @engineshed Great atmosphere at the British Li...       0  
10834  Cramer: Iger's 3 words that wrecked Disney's s...       0  

[7552 rows x 4 columns]

## 0. Data Preprocessing

### 0.1 Data Cleaning

In [4]:
stop_words = stopwords.words('english')
porter = PorterStemmer()

In [5]:
def processing (sentence):
    result = sentence.lower() #Lower case 
    result = re.sub(r'\d+', '', result) #Removing numbers
    result = result.translate(str.maketrans('', '', string.punctuation)) #Remove weird characters
    result = result.strip() #Eliminate blanks from begining and end of setences
    result = result.split() #Separate into words
    result = [w for w in result if not w in stop_words] #Eliminate stop_words
    result = [porter.stem(word) for word in result] #Stem Words
    return (result)

In [6]:
text = list(twt["text"])
processing(text[0])

['deed', 'reason', 'earthquak', 'may', 'allah', 'forgiv', 'us']

### 0.2 Embeding

In [7]:
word2vec = gensim.models.KeyedVectors.load_word2vec_format("GoogleNews-vectors-negative300.bin.gz", binary=True)

In [8]:
def tweet_vec (tweet, word2vec):
    word_vecs = [word2vec.get_vector(w) for w in tweet if w in word2vec.vocab]
#     print(tweet)
#     print('Number of words: {}'.format(len(word_vecs)))
    if len(word_vecs) > 1:
        return np.stack(word_vecs).mean(0)
    else:
        return None

In [9]:
prep_text = [processing(i) for i in text]

In [10]:
final_data = []

# prep_text[0]
# tweet_vec(prep_text[0], word2vec)
for i in prep_text:
    vec = tweet_vec(i,word2vec)
    if vec is not None:    
        final_data.append(vec)

In [14]:
final_data

[array([ 1.54663086e-01,  1.65893547e-02,  1.05923459e-01,  1.29199222e-01,
        -9.18945298e-02,  2.65991203e-02,  1.30187988e-01,  3.63037102e-02,
         3.74023430e-02,  1.81738287e-01, -8.16406235e-02, -1.56250000e-01,
        -1.79150388e-01,  9.73205566e-02, -2.04296872e-01,  1.47558600e-01,
         1.03283688e-01,  3.53027359e-02, -5.47363274e-02, -8.53881836e-02,
         4.61181626e-02,  4.24072258e-02,  1.31445318e-01, -1.21093746e-02,
         1.07421875e-02,  1.31835938e-02, -3.77929695e-02,  3.95019539e-02,
        -1.12548828e-01, -3.12988274e-02,  1.01074222e-02, -1.48681644e-02,
        -5.93872070e-02,  2.44262703e-02,  4.10156250e-02,  1.26655579e-01,
         6.01074211e-02, -4.80957031e-02,  1.09387204e-01, -1.25732424e-03,
         1.16748050e-01,  1.77368168e-02,  1.29492193e-01, -5.02929697e-03,
         8.05908218e-02, -1.74218744e-01,  1.90429692e-03, -6.63330108e-02,
        -1.33105472e-01, -1.16357423e-01, -9.32617188e-02,  1.18164066e-02,
         1.1

## 1. NN construction

In [11]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

class Net(nn.Module):

    def __init__(self):
        super(Net, self).__init__()
        self.fc1 = nn.Linear(300,300)  # 6*6 from image dimension
        self.fc2 = nn.Linear(300, 2)
        self.softmax =  nn.Softmax()

    def forward(self, x):
        x = F.relu(self.fc1(x))
        # If the size is a square you can only specify a single number
        x = F.relu(self.fc2(x))
#         x = x.view(-1, self.num_flat_features(x))
#         x = F.relu(self.fc1(x))
#         x = F.relu(self.fc2(x))
#         x = self.fc3(x)
        x = self.softmax(x)
        return x

    def num_flat_features(self, x):
        size = x.size()[1:]  # all dimensions except the batch dimension
        num_features = 1
        for s in size:
            num_features *= s
        return num_features

    if __name__ == '__init__':
        
        for epoch in range(2):  # loop over the dataset multiple times

    running_loss = 0.0
    for i, data in enumerate(trainloader, 0):
        # get the inputs; data is a list of [inputs, labels]
        inputs, labels = data

        # zero the parameter gradients
        optimizer.zero_grad()

        # forward + backward + optimize
        outputs = net(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()

        # print statistics
        running_loss += loss.item()
        if i % 2000 == 1999: # print every 2000 mini-batches
            print('[%d, %5d] loss: %.3f' % (epoch + 1, i + 1, running_loss / 2000))
            running_loss = 0.0

print('Finished Training')

net = Net()
print(net)

# create your optimizer
optimizer = optim.SGD(net.parameters(), lr=0.01)

# in your training loop:
optimizer.zero_grad()   # zero the gradient buffers
output = net(input)
loss = criterion(output, target)
loss.backward()
optimizer.step()    # Does the update

IndentationError: expected an indented block (<ipython-input-11-38c93d84cbd3>, line 36)